In [22]:
import numpy as np
import pandas as pd
from tqdm.notebook import tqdm
from sklearn.metrics import mean_absolute_error
import optuna
from concurrent.futures import ProcessPoolExecutor
from joblib import Parallel, delayed
from scipy.stats import t


In [2]:
Main_data=pd.read_csv('Main_data.csv')
Schedule=pd.read_csv('Schedule.csv')
Origin_result = pd.read_csv('Origin_result.csv')
Main_data.columns

Index(['Team', 'Conference', '2PA', '3PA', 'TOV', 'FTD', 'RAA', 'PZA', 'MRA',
       'COA', 'ABA', '2SFD', '3SFD', 'NSFD', 'RAP', 'PZP', 'MRP', 'COP', 'ABP',
       'FTP', 'PACE', 'DEEPA', 'DEEPP', '2PAnd1', '3PAnd1', 'ORAP', 'OPZP',
       'OMRP', 'OCOP', 'OABP', 'ORB', 'DRB'],
      dtype='object')

In [3]:
def generate_dirichlet_sample(row,multiply):
    ratios = row[['2PA', '3PA', 'FTD', 'TOV']].values
    ratios = ratios.flatten()
    
    alpha_raw = ratios  
    alpha = (alpha_raw / alpha_raw.sum()) * multiply  
    
    dirichlet_sample = np.random.dirichlet(alpha)

    return dirichlet_sample

def generate_dirichlet_sample_2pt(row,multiply):
    ratios = row[['RAA', 'PZA', 'MRA', '2PAnd1']].values
    ratios = ratios.flatten()
    
    alpha_raw = ratios 
    alpha = (alpha_raw / alpha_raw.sum()) * multiply  

    dirichlet_sample_2pt = np.random.dirichlet(alpha)

    return dirichlet_sample_2pt

def generate_dirichlet_sample_3pt(row,multiply):
    ratios = row[['COA', 'ABA', 'DEEPA', '3PAnd1']].values
    ratios = ratios.flatten()
    
    alpha_raw = ratios  
    alpha = (alpha_raw / alpha_raw.sum()) * multiply  

    dirichlet_sample_3pt = np.random.dirichlet(alpha)

    return dirichlet_sample_3pt

def generate_dirichlet_sample_FT(row,multiply):
    
    ratios = row[['2SFD', '3SFD', 'NSFD']].values
    ratios = ratios.flatten()
    
    alpha_raw = ratios 
    alpha = (alpha_raw / alpha_raw.sum()) * multiply  

    dirichlet_sample_FT = np.random.dirichlet(alpha)

    return dirichlet_sample_FT

In [4]:
def generate_indicator(sample_dist):
        cumulative_probs = np.cumsum(sample_dist)

        random_value = np.random.uniform(0, 1)

        if random_value <= cumulative_probs[0]:
            return '2pt'
        elif random_value <= cumulative_probs[1]:
            return '3pt'
        elif random_value <= cumulative_probs[2]:
            return 'FT'
        else:
            return 'TOV'
            
def generate_indicator_2pt(sample_dist):
        cumulative_probs = np.cumsum(sample_dist)

        random_value = np.random.uniform(0, 1)

        if random_value <= cumulative_probs[0]:
            return 'RA'
        elif random_value <= cumulative_probs[1]:
            return 'PZ'
        elif random_value <= cumulative_probs[2]:
            return 'MR'
        else:
            return '2PAnd1'

def generate_indicator_3pt(sample_dist):
        cumulative_probs = np.cumsum(sample_dist)

        random_value = np.random.uniform(0, 1)

        if random_value <= cumulative_probs[0]:
            return 'CO'
        elif random_value <= cumulative_probs[1]:
            return 'AB'
        elif random_value <= cumulative_probs[2]:
            return 'DEEP'
        else:
            return '3PAnd1'

def generate_indicator_FT(sample_dist):
        cumulative_probs = np.cumsum(sample_dist)

        random_value = np.random.uniform(0, 1)

        if random_value <= cumulative_probs[0]:
            return '2SFD'
        elif random_value <= cumulative_probs[1]:
            return '3SFD'
        else:
            return 'NSFD'

In [5]:
def simulation_function(OFF, DEF, rate, multiply, maindata):
    off_team_data = maindata[maindata['Team'] == OFF]
    def_team_data = maindata[maindata['Team'] == DEF]

    if off_team_data.empty or def_team_data.empty:
        raise ValueError("Name_error")

    sample_dist = generate_dirichlet_sample(off_team_data, multiply)
    indicator = generate_indicator(sample_dist)

    retry_occurred = False
    nested_result = None  

    if indicator == '2pt':
        sample_dist_step2 = generate_dirichlet_sample_2pt(off_team_data, multiply)
        indicator_step2 = generate_indicator_2pt(sample_dist_step2)
        if indicator_step2 == 'RA':
            success_prob = ((rate * off_team_data['RAP'].iloc[0]) + ((1-rate) * def_team_data['ORAP'].iloc[0])) / 100
            random_value = np.random.uniform(0, 1)
            if random_value <= success_prob:
                point = 2
            else:
                point = 0
            if point == 0:
                off_orb = off_team_data['ORB'].iloc[0]
                def_drb = def_team_data['DRB'].iloc[0]
                total = off_orb + def_drb
                prob_retry = off_orb / total if total > 0 else 0
                prob_fail = def_drb / total if total > 0 else 1

                retry_prob = np.random.uniform(0, 1)
                if retry_prob <= prob_retry:
                    retry_occurred = True
                    nested_result = simulation_function(OFF, DEF, rate, multiply, maindata)
                else:
                    point = 0

        elif indicator_step2 == 'PZ':
            success_prob = ((rate * off_team_data['PZP'].iloc[0]) + ((1-rate) * def_team_data['OPZP'].iloc[0])) / 100
            random_value = np.random.uniform(0, 1)
            if random_value <= success_prob:
                point = 2
            else:
                point = 0
            if point == 0:
                off_orb = off_team_data['ORB'].iloc[0]
                def_drb = def_team_data['DRB'].iloc[0]
                total = off_orb + def_drb
                prob_retry = off_orb / total if total > 0 else 0
                prob_fail = def_drb / total if total > 0 else 1

                retry_prob = np.random.uniform(0, 1)
                if retry_prob <= prob_retry:
                    retry_occurred = True
                    nested_result = simulation_function(OFF, DEF, rate, multiply, maindata)
                else:
                    point = 0

        elif indicator_step2 == 'MR':
            success_prob = ((rate * off_team_data['MRP'].iloc[0]) + ((1-rate) * def_team_data['OMRP'].iloc[0])) / 100
            random_value = np.random.uniform(0, 1)
            if random_value <= success_prob:
                point = 2
            else:
                point = 0
            if point == 0:
                off_orb = off_team_data['ORB'].iloc[0]
                def_drb = def_team_data['DRB'].iloc[0]
                total = off_orb + def_drb
                prob_retry = off_orb / total if total > 0 else 0
                prob_fail = def_drb / total if total > 0 else 1

                retry_prob = np.random.uniform(0, 1)
                if retry_prob <= prob_retry:
                    retry_occurred = True
                    nested_result = simulation_function(OFF, DEF, rate, multiply, maindata)
                else:
                    point = 0

        else:
            success_prob = (off_team_data['FTP'].iloc[0] / 100)
            random_value = np.random.uniform(0, 1)
            if random_value <= success_prob:
                point = 3
            else:
                point = 2
                off_orb = off_team_data['ORB'].iloc[0]
                def_drb = def_team_data['DRB'].iloc[0]
                total = off_orb + def_drb
                prob_retry = off_orb / total if total > 0 else 0
                prob_fail = def_drb / total if total > 0 else 1

                retry_prob = np.random.uniform(0, 1)
                if retry_prob <= prob_retry:
                    retry_occurred = True
                    nested_result = simulation_function(OFF, DEF, rate, multiply, maindata)
                else:
                    point = 2

    elif indicator == '3pt':
        sample_dist_step2 = generate_dirichlet_sample_3pt(off_team_data, multiply)
        indicator_step2 = generate_indicator_3pt(sample_dist_step2)
        if indicator_step2 == 'CO':
            success_prob = ((rate * off_team_data['COP'].iloc[0]) + ((1-rate) * def_team_data['OCOP'].iloc[0])) / 100
            random_value = np.random.uniform(0, 1)
            if random_value <= success_prob:
                point = 3
            else:
                point = 0
            if point == 0:
                off_orb = off_team_data['ORB'].iloc[0]
                def_drb = def_team_data['DRB'].iloc[0]
                total = off_orb + def_drb
                prob_retry = off_orb / total if total > 0 else 0
                prob_fail = def_drb / total if total > 0 else 1

                retry_prob = np.random.uniform(0, 1)
                if retry_prob <= prob_retry:
                    retry_occurred = True
                    nested_result = simulation_function(OFF, DEF, rate, multiply, maindata)
                else:
                    point = 0

        elif indicator_step2 == 'AB':
            success_prob = ((rate * off_team_data['ABP'].iloc[0]) + ((1-rate) * def_team_data['OABP'].iloc[0])) / 100
            random_value = np.random.uniform(0, 1)
            if random_value <= success_prob:
                point = 3
            else:
                point = 0
            if point == 0:
                off_orb = off_team_data['ORB'].iloc[0]
                def_drb = def_team_data['DRB'].iloc[0]
                total = off_orb + def_drb
                prob_retry = off_orb / total if total > 0 else 0
                prob_fail = def_drb / total if total > 0 else 1

                retry_prob = np.random.uniform(0, 1)
                if retry_prob <= prob_retry:
                    retry_occurred = True
                    nested_result = simulation_function(OFF, DEF, rate, multiply, maindata)
                else:
                    point = 0

        elif indicator_step2 == 'DEEP':
            success_prob = (off_team_data['DEEPP'].iloc[0] / 100)
            random_value = np.random.uniform(0, 1)
            if random_value <= success_prob:
                point = 3
            else:
                point = 0
            if point == 0:
                off_orb = off_team_data['ORB'].iloc[0]
                def_drb = def_team_data['DRB'].iloc[0]
                total = off_orb + def_drb
                prob_retry = off_orb / total if total > 0 else 0
                prob_fail = def_drb / total if total > 0 else 1

                retry_prob = np.random.uniform(0, 1)
                if retry_prob <= prob_retry:
                    retry_occurred = True
                    nested_result = simulation_function(OFF, DEF, rate, multiply, maindata)
                else:
                    point = 0

        else:
            success_prob = (off_team_data['FTP'].iloc[0] / 100)
            random_value = np.random.uniform(0, 1)
            if random_value <= success_prob:
                point = 4
            else:
                point = 3
                off_orb = off_team_data['ORB'].iloc[0]
                def_drb = def_team_data['DRB'].iloc[0]
                total = off_orb + def_drb
                prob_retry = off_orb / total if total > 0 else 0
                prob_fail = def_drb / total if total > 0 else 1

                retry_prob = np.random.uniform(0, 1)
                if retry_prob <= prob_retry:
                    retry_occurred = True
                    nested_result = simulation_function(OFF, DEF, rate, multiply, maindata)
                else:
                    point = 3

    elif indicator == 'FT':
        sample_dist_step2 = generate_dirichlet_sample_FT(off_team_data, multiply)
        indicator_step2 = generate_indicator_FT(sample_dist_step2)
        if indicator_step2 == '2SFD':
            success_prob = off_team_data['FTP'].iloc[0] / 100
            point = 0
            last_shot_success = True
            for _ in range(2):
                random_value = np.random.uniform(0, 1)
                if random_value <= success_prob:
                    point += 1
                    last_shot_success = True
                else:
                    last_shot_success = False

            if not last_shot_success:
                off_orb = off_team_data['ORB'].iloc[0]
                def_drb = def_team_data['DRB'].iloc[0]
                total = off_orb + def_drb
                prob_retry = off_orb / total if total > 0 else 0
                prob_fail = def_drb / total if total > 0 else 1

                retry_prob = np.random.uniform(0, 1)
                if retry_prob <= prob_retry:
                    retry_occurred = True
                    nested_result = simulation_function(OFF, DEF, rate, multiply, maindata)
                else:
                    point = point

        elif indicator_step2 == '3SFD':
            success_prob = off_team_data['FTP'].iloc[0] / 100
            point = 0
            last_shot_success = True
            for _ in range(3):
                random_value = np.random.uniform(0, 1)
                if random_value <= success_prob:
                    point += 1
                    last_shot_success = True
                else:
                    last_shot_success = False

            if not last_shot_success:
                off_orb = off_team_data['ORB'].iloc[0]
                def_drb = def_team_data['DRB'].iloc[0]
                total = off_orb + def_drb
                prob_retry = off_orb / total if total > 0 else 0
                prob_fail = def_drb / total if total > 0 else 1

                retry_prob = np.random.uniform(0, 1)
                if retry_prob <= prob_retry:
                    retry_occurred = True
                    nested_result = simulation_function(OFF, DEF, rate, multiply, maindata)
                else:
                    point = point

        else:
            success_prob = off_team_data['FTP'].iloc[0] / 100
            point = 0
            last_shot_success = True
            for _ in range(2):
                random_value = np.random.uniform(0, 1)
                if random_value <= success_prob:
                    point += 1
                    last_shot_success = True
                else:
                    last_shot_success = False

            if not last_shot_success:
                off_orb = off_team_data['ORB'].iloc[0]
                def_drb = def_team_data['DRB'].iloc[0]
                total = off_orb + def_drb
                prob_retry = off_orb / total if total > 0 else 0
                prob_fail = def_drb / total if total > 0 else 1

                retry_prob = np.random.uniform(0, 1)
                if retry_prob <= prob_retry:
                    retry_occurred = True
                    nested_result = simulation_function(OFF, DEF, rate, multiply, maindata)
                else:
                    point = point

    else:
        indicator_step2 = 'TOV'
        point = 0

    result = {
        'indicator_step1': indicator,
        'indicator_step2': indicator_step2,
        'point': point,
        'retry_occurred': retry_occurred
    }

    if nested_result is not None:
        result['nested_result'] = nested_result
        result['point'] += nested_result.get('point', 0)

    return result

### PACE

In [6]:
def game_simulation_function (OFF, DEF, rate, multiply, maindata):
    off_team_data = maindata[maindata['Team'] == OFF]
    def_team_data = maindata[maindata['Team'] == DEF]
    n=int((off_team_data['PACE'].iloc[0] + def_team_data['PACE'].iloc[0])/2)
    total_points = 0
    for _ in range(n):
        total_points += simulation_function(OFF, DEF, rate, multiply, maindata)['point']

    return total_points

In [7]:
def schedule_simulation(schedule, rate, multiply, maindata):
    wins = [] 
    loses = [] 

    for _, row in tqdm(schedule.iterrows(), total=len(schedule), desc="Simulating Games"):
        visitor = row['Visitor']
        home = row['Home']

        visitor_off_points = game_simulation_function(visitor, home, rate, multiply, maindata)

        home_off_points = game_simulation_function(home, visitor, rate, multiply, maindata)

        while visitor_off_points == home_off_points:
            visitor_off_points = game_simulation_function(visitor, home, rate, multiply, maindata)
            home_off_points = game_simulation_function(home, visitor, rate, multiply, maindata)

        if visitor_off_points > home_off_points:
            wins.append(visitor)
            loses.append(home)
        else:
            wins.append(home)
            loses.append(visitor)

    schedule['Win'] = wins
    schedule['Lose'] = loses
    return schedule


In [8]:
def schedule_simulation_basic(schedule, rate, multiply, maindata):
    wins = []  
    loses = []  

    for _, row in schedule.iterrows():
        visitor = row['Visitor']
        home = row['Home']

        visitor_off_points = game_simulation_function(visitor, home, rate, multiply, maindata)

        home_off_points = game_simulation_function(home, visitor, rate, multiply, maindata)

        while visitor_off_points == home_off_points:
            visitor_off_points = game_simulation_function(visitor, home, rate, multiply, maindata)
            home_off_points = game_simulation_function(home, visitor, rate, multiply, maindata)

        if visitor_off_points > home_off_points:
            wins.append(visitor)
            loses.append(home)
        else:
            wins.append(home)
            loses.append(visitor)

    schedule['Win'] = wins
    schedule['Lose'] = loses
    return schedule


In [9]:
def process_game(row, rate, multiply, maindata):
    visitor = row['Visitor']
    home = row['Home']

    visitor_off_points = game_simulation_function(visitor, home, rate, multiply, maindata)

    home_off_points = game_simulation_function(home, visitor, rate, multiply, maindata)

    while visitor_off_points == home_off_points:
        visitor_off_points = game_simulation_function(visitor, home, rate, multiply, maindata)
        home_off_points = game_simulation_function(home, visitor, rate, multiply, maindata)

    if visitor_off_points > home_off_points:
        return visitor, home
    else:
        return home, visitor

def schedule_simulation_parallel(schedule, rate, multiply, maindata, n_jobs=-1):
    results = Parallel(n_jobs=n_jobs)(
        delayed(process_game)(row, rate, multiply, maindata) for _, row in tqdm(schedule.iterrows(), total=len(schedule), desc="Simulating Games")
    )

    wins, loses = zip(*results)
    schedule['Win'] = wins
    schedule['Lose'] = loses
    return schedule


In [10]:
def schedule_simulation_ntimes(n, schedule, rate, multiply, maindata):
    expanded_schedules = []  

    for i in range(n):

        print(f"Simulation {i + 1}/{n}")
        simulated_schedule = schedule_simulation_parallel(schedule.copy(), rate, multiply, maindata)
        simulated_schedule['Simulation'] = i + 1  
        expanded_schedules.append(simulated_schedule)

    combined_schedule = pd.concat(expanded_schedules, ignore_index=True)
    return combined_schedule


In [11]:
def calculate_win_percentage(schedule, main_data):
    import pandas as pd

    win_counts = schedule['Win'].value_counts()  
    lose_counts = schedule['Lose'].value_counts()  

    game_counts = win_counts.add(lose_counts, fill_value=0)  

    win_percentage = (win_counts / game_counts).fillna(0) 

    win_percentage_table = pd.DataFrame({
        'Team': win_counts.index.union(lose_counts.index), 
        'Conference': win_counts.index.union(lose_counts.index).map(main_data.set_index('Team')['Conference']),  # Conference 추가
        'Wins': win_counts,  
        'Losses': lose_counts,  
        'Win_Percentage': win_percentage  
    }).fillna(0)  

    win_percentage_table['Wins'] = win_percentage_table['Wins'].astype(int)
    win_percentage_table['Losses'] = win_percentage_table['Losses'].astype(int)

    win_percentage_table['Play_off'] = 0  
    win_percentage_table.loc[win_percentage_table.groupby('Conference')['Win_Percentage']
                             .rank(method='first', ascending=False) <= 10, 'Play_off'] = 1

    win_percentage_table = win_percentage_table.reset_index(drop=True)

    return win_percentage_table


In [12]:
from sklearn.metrics import mean_absolute_error

def calculate_mae(result_sample, origin_result):
    if isinstance(result_sample, pd.Series):
        result_sample = result_sample.reset_index()
        result_sample.columns = ['Team', 'Win_Percentage']

    if isinstance(origin_result, pd.Series):
        origin_result = origin_result.reset_index()
        origin_result.columns = ['Team', 'Win_Percentage']

    comparison_df = result_sample.merge(origin_result, on='Team', suffixes=('_Sample', '_Origin'))

    mae = mean_absolute_error(
        comparison_df['Win_Percentage_Sample'], 
        comparison_df['Win_Percentage_Origin']
    )
    return mae


In [13]:
def calculate_play_off_accuracy(predicted_result, origin_result):
    import pandas as pd

    merged = predicted_result[['Team', 'Play_off']].merge(origin_result[['Team', 'Play_off']], on='Team', suffixes=('_predicted', '_actual'))

    accuracy = (merged['Play_off_predicted'] == merged['Play_off_actual']).mean()

    return accuracy


In [15]:
import pandas as pd

def objective(trial):
    rate = trial.suggest_float("rate", 0.5, 1.0, step=0.01)
    multiply = trial.suggest_int("multiply", 10, 200, step=1)

    accuracies = []
    maes = []
    team_comparison_list = []

    for season in range(1, 51):
        exam_n = schedule_simulation_ntimes(1, Schedule, rate, multiply, Main_data)

        sample = calculate_win_percentage(exam_n, Main_data)
        accuracy = calculate_play_off_accuracy(sample, Origin_result)
        mae = calculate_mae(sample, Origin_result)

        accuracies.append(accuracy)
        maes.append(mae)

        comparison = sample[['Team', 'Win_Percentage', 'Play_off']].merge(
            Origin_result[['Team', 'Win_Percentage', 'Play_off']],
            on='Team',
            suffixes=('_sim', '_origin')
        )
        comparison['MAE'] = abs(comparison['Win_Percentage_sim'] - comparison['Win_Percentage_origin'])
        comparison['Play_off_Correct'] = (comparison['Play_off_sim'] == comparison['Play_off_origin']).astype(int)

        comparison['Season'] = season

        team_comparison_list.append(comparison)

    avg_accuracy = sum(accuracies) / len(accuracies)
    std_accuracy = pd.Series(accuracies).std()
    avg_mae = sum(maes) / len(maes)
    std_mae = pd.Series(maes).std()

    combined_comparison = pd.concat(team_comparison_list)

    team_results = combined_comparison.groupby('Team').agg({
        'MAE': ['mean', 'std'],
        'Play_off_Correct': ['mean', 'std']
    }).reset_index()
    
    team_results.columns = ['Team', 'MAE_mean', 'MAE_std', 'Play_off_Accuracy (%)', 'Play_off_Correct_std']
    team_results['Play_off_Accuracy (%)'] *= 100  
    team_results['Play_off_Correct_std'] *= 100  

    trial.set_user_attr("season_results", combined_comparison)
    trial.set_user_attr("team_results", team_results)
    trial.set_user_attr("average_accuracy", avg_accuracy)
    trial.set_user_attr("std_accuracy", std_accuracy)
    trial.set_user_attr("average_mae", avg_mae)
    trial.set_user_attr("std_mae", std_mae)

    return avg_accuracy  

study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=100) 

best_trial = study.best_trial
best_season_results = best_trial.user_attrs["season_results"]
best_team_results = best_trial.user_attrs["team_results"]
best_avg_accuracy = best_trial.user_attrs["average_accuracy"]
best_std_accuracy = best_trial.user_attrs["std_accuracy"]
best_avg_mae = best_trial.user_attrs["average_mae"]
best_std_mae = best_trial.user_attrs["std_mae"]

best_season_results.to_csv("best_season_results.xlsx", index=False)

print("\nBest parameters:", study.best_params)
print(f"Best average accuracy: {best_avg_accuracy:.4f} ± {best_std_accuracy:.4f}")
print(f"Best average MAE: {best_avg_mae:.4f} ± {best_std_mae:.4f}")
print("\nBest team results:")
print(best_team_results.to_string(index=False))
print("\nSeason results have been saved as 'best_season_results.xlsx'.")


[I 2025-02-03 17:41:43,345] A new study created in memory with name: no-name-4da532eb-ffc0-42f9-b23e-339a364c7be6


Simulation 1/1


Simulating Games:   0%|          | 0/1230 [00:00<?, ?it/s]

Simulation 1/1


Simulating Games:   0%|          | 0/1230 [00:00<?, ?it/s]

...

Simulating Games:   0%|          | 0/1230 [00:00<?, ?it/s]

Simulation 1/1


Simulating Games:   0%|          | 0/1230 [00:00<?, ?it/s]

[I 2025-02-05 01:50:08,510] Trial 199 finished with value: 0.8173333333333335 and parameters: {'rate': 0.88, 'multiply': 145}. Best is trial 8 with value: 0.8506666666666665.


ModuleNotFoundError: No module named 'openpyxl'

In [27]:
best_season_results.to_csv("best_season_results.csv", index=False)